# AIRL on Robosuite Franka Panda Lift

This notebook samples expert trajectories from a pretrained robomimic policy (Franka Panda Lift), trains AIRL to learn a reward, and uses that reward to train a PPO agent on the Lift task.

In [1]:
# Ensure required packages are installed (gymnasium, stable-baselines3, torchvision, transformers, imitation, huggingface_hub pinned)
import importlib, sys, subprocess

def _ensure(pkg_import_name, pip_id):
    try:
        importlib.import_module(pkg_import_name)
        print(f"{pip_id} already installed")
    except Exception:
        print(f"Installing {pip_id} ...")
        subprocess.check_call([sys.executable, "-m", "pip", "install", pip_id])

# Robust installer that forces a version
def _install(pip_id):
    print(f"Installing {pip_id} ...")
    subprocess.check_call([sys.executable, "-m", "pip", "install", pip_id])

# Gymnasium is required by robosuite GymWrapper and imitation
_ensure("gymnasium", "gymnasium==0.29.1")
# Stable-Baselines3 for PPO (will upgrade torch to a compatible version)
_ensure("stable_baselines3", "stable-baselines3>=2.3.0")
# TorchVision required by robomimic model building utils
_ensure("torchvision", "torchvision")
# Transformers required by robomimic.lang_utils
_ensure("transformers", "transformers")
# Imitation learning algorithms
_ensure("imitation", "imitation")
# TensorBoard for SB3 logging/plots
_ensure("tensorboard", "tensorboard")
# Pin huggingface_hub for robomimic compatibility
_install("huggingface_hub==0.23.4")


gymnasium==0.29.1 already installed
stable-baselines3>=2.3.0 already installed
torchvision already installed
transformers already installed
imitation already installed
tensorboard already installed
Installing huggingface_hub==0.23.4 ...


/home/chris/miniconda3/envs/env_lift/lib/python3.11/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: 'Could not load this library: /home/chris/miniconda3/envs/env_lift/lib/python3.11/site-packages/torchvision/image.so'If you don't plan on using image functionality from `torchvision.io`, you can ignore this warning. Otherwise, there might be something wrong with your environment. Did you have `libjpeg` or `libpng` installed before building `torchvision` from source?
  warn(


In [2]:
import os
import urllib.request
from copy import deepcopy
from typing import List, Dict, Any

import numpy as np
import torch

import robosuite
from robosuite.wrappers.gym_wrapper import GymWrapper

from gymnasium import spaces

from stable_baselines3 import PPO
from stable_baselines3.ppo import MultiInputPolicy
from stable_baselines3.common.vec_env import DummyVecEnv
from stable_baselines3.common.evaluation import evaluate_policy

from imitation.data.types import TrajectoryWithRew, DictObs
from imitation.algorithms.adversarial.airl import AIRL
from imitation.rewards.reward_nets import BasicShapedRewardNet
from imitation.util.networks import RunningNorm

SEED = 42
np.random.seed(SEED)
torch.manual_seed(SEED)

# Config
N_EXPERT_EPISODES = 300  # number of expert episodes to collect
ROLLOUT_HORIZON = 400    # max steps per expert rollout
N_ENVS = 4               # vectorized envs for PPO training
FAST = False              # set False for longer training
N_RL_TRAIN_STEPS =200_000 if FAST else 1_000_000

[robosuite WARNING] No private macro file found! (macros.py:57)
[robosuite WARNING] It is recommended to use a private macro file (macros.py:58)
[robosuite WARNING] To setup, run: python /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/scripts/setup_macros.py (macros.py:59)
[robosuite WARNING] Could not import robosuite_models. Some robots may not be available. If you want to use these robots, please install robosuite_models from source (https://github.com/ARISE-Initiative/robosuite_models) or through pip install. (__init__.py:30)


## Download and load pretrained expert (robomimic model zoo)

In [ ]:
# Download pretrained checkpoint (Lift, Proficient Human, low-dim)

ckpt_path = "lift_ph_low_dim_epoch_1000_succ_100.pth"

USE_POLICY = False
expert_policy = None
expert_env = None

try:
    import robomimic.utils.file_utils as FileUtils
    import robomimic.utils.torch_utils as TorchUtils
    from robomimic.algo import RolloutPolicy

    if not os.path.exists(ckpt_path):
        url = (
            "http://downloads.cs.stanford.edu/downloads/rt_benchmark/model_zoo/lift/bc_rnn/"
            "lift_ph_low_dim_epoch_1000_succ_100.pth"
        )
        print(f'Downloading pretrained expert from {url} ...')
        urllib.request.urlretrieve(url, filename=ckpt_path)
    assert os.path.exists(ckpt_path), 'Failed to fetch expert checkpoint'

    # Restore policy and its training metadata
    device = TorchUtils.get_torch_device(try_to_use_cuda=True)
    expert_policy, ckpt_dict = FileUtils.policy_from_checkpoint(
        ckpt_path=ckpt_path, device=device, verbose=True
    )

    # Create the corresponding robomimic environment (EnvBase)
    try:
        expert_env, _ = FileUtils.env_from_checkpoint(
            ckpt_dict=ckpt_dict,
            render=False,
            render_offscreen=False,
            verbose=True,
        )
        USE_POLICY = True
        print("Using robomimic expert policy + env for rollouts.")
    except Exception as env_e:
        print("Creating env from checkpoint failed:", repr(env_e))
        USE_POLICY = False
except Exception as e:
    print("Robomimic expert import failed:", repr(e))
    USE_POLICY = False

# If expert policy / env is not available, ensure dataset fallback is ready
if not USE_POLICY:
    import h5py
    hf_url = "https://huggingface.co/datasets/amandlek/robomimic/resolve/main/v1.5/lift/ph/low_dim_v15.hdf5?download=true"
    demo_local = "lift_ph_low_dim_v15.hdf5"
    if not os.path.exists(demo_local):
        print(f"Downloading demos from {hf_url} ...")
        try:
            urllib.request.urlretrieve(hf_url, filename=demo_local)
        except Exception as dl_e:
            print("Download from HuggingFace failed:", repr(dl_e))
    if os.path.exists(demo_local):
        print("Dataset fallback available at", demo_local)
    else:
        print("Dataset fallback not available; please download the file manually and re-run.")

## Collect expert trajectories
We'll run the expert policy for several episodes to build demonstration trajectories for AIRL.

In [3]:
# Fallback: download Lift PH low-dim dataset from HuggingFace and parse, if expert env failed
try:
    USE_POLICY
except NameError:
    USE_POLICY = False

if not USE_POLICY:
    import os
    import urllib.request
    import h5py
    import numpy as np

    hf_url = "https://huggingface.co/datasets/amandlek/robomimic/resolve/main/v1.5/lift/ph/low_dim_v15.hdf5?download=true"
    try:
        demo_local
    except NameError:
        demo_local = "lift_ph_low_dim_v15.hdf5"

    if not os.path.exists(demo_local):
        print(f"Downloading demos from {hf_url} ...")
        urllib.request.urlretrieve(hf_url, filename=demo_local)
    assert os.path.exists(demo_local), "Failed to download demos from HuggingFace"

    def load_expert_from_hdf5(h5_path, max_episodes):
        """Load episodes from robomimic low-dim hdf5 into raw_expert format.
        Returns a list of dicts with keys: obs (list of dicts, T+1), acts (T,d), rews (T,), dones (T,).
        """
        episodes = []
        with h5py.File(h5_path, "r") as f:
            data_grp = f["data"]
            ep_keys = sorted(list(data_grp.keys()))
            if max_episodes is not None:
                ep_keys = ep_keys[:max_episodes]
            for k in ep_keys:
                g = data_grp[k]
                actions = g["actions"][()].astype(np.float32)
                T = actions.shape[0]
                # Rewards and dones/terminals may or may not be present
                rews = g.get("rewards")
                rews = (rews[()].astype(np.float32) if rews is not None else np.zeros((T,), dtype=np.float32))
                terminals = g.get("terminals") or g.get("dones")
                dones = (terminals[()].astype(bool) if terminals is not None else np.zeros((T,), dtype=bool))
                # Observations group
                obs_group = g["obs"]
                obs_keys = list(obs_group.keys())
                obs_list = []
                # Some datasets store T or T+1 obs per key; be robust
                for t in range(T + 1):
                    obs_t = {}
                    for name in obs_keys:
                        arr = obs_group[name]
                        # choose index within bounds
                        idx = min(t, arr.shape[0] - 1)
                        obs_t[name] = np.array(arr[idx])
                    obs_list.append(obs_t)
                episodes.append({
                    "obs": obs_list,
                    "acts": actions,
                    "rews": rews,
                    "dones": dones,
                })
        return episodes

    RAW_EXPERT_FROM_DATASET = load_expert_from_hdf5(demo_local, max_episodes=N_EXPERT_EPISODES)
    print(f"Loaded {len(RAW_EXPERT_FROM_DATASET)} demos from dataset.")
else:
    print("Expert policy and env available; skipping dataset fallback.")

Loaded 200 demos from dataset.


In [4]:
def collect_expert_rollouts(env, policy, n_episodes: int, horizon: int):
    raw_trajs = []
    for ep in range(n_episodes):
        obs = env.reset()
        # Optional robosuite determinism hack from robomimic examples
        try:
            state_dict = env.get_state()
            obs = env.reset_to(state_dict)
        except Exception:
            pass
        obs_list: List[Dict[str, np.ndarray]] = [deepcopy(obs)]
        acts: List[np.ndarray] = []
        rews: List[float] = []
        infos: List[Dict[str, Any]] = []
        for t in range(horizon):
            act = policy(ob=obs)
            next_obs, r, done, info = env.step(act)
            acts.append(np.asarray(act))
            rews.append(float(r))
            infos.append(info)
            obs_list.append(deepcopy(next_obs))
            obs = next_obs
            if done:
                break
        raw_trajs.append(dict(obs_list=obs_list, acts=acts, rews=rews, infos=infos))
    return raw_trajs

# Build raw_expert depending on whether we have the policy or not
if USE_POLICY:
    raw_expert = collect_expert_rollouts(expert_env, expert_policy, N_EXPERT_EPISODES, ROLLOUT_HORIZON)
else:
    raw_expert = RAW_EXPERT_FROM_DATASET

len(raw_expert), sum(len(t['acts']) for t in raw_expert)

(200, 9666)

## Build a Gym-compatible robosuite Lift environment
We wrap robosuite's Lift task with GymWrapper (dict observations) and vectorize it for SB3.

In [5]:
# Peek at robosuite Lift observation dict keys to align dataset/env
import robosuite as suite
rs_env_tmp = suite.make(
    "Lift",
    robots=["Panda"],
    use_camera_obs=False,
    use_object_obs=True,
    has_offscreen_renderer=False,
    has_renderer=False,
    control_freq=20,
    horizon=200,
    reward_shaping=True,
)
obs0 = rs_env_tmp.reset()
print(sorted(list(obs0.keys())))
print({k: obs0[k].shape for k in obs0.keys() if isinstance(obs0[k], (list, tuple, type(obs0[next(iter(obs0))])))})
rs_env_tmp.close()

[robosuite INFO] Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json (composite_controller_factory.py:121)
[robosuite INFO] Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json (composite_controller_factory.py:121)


['cube_pos', 'cube_quat', 'gripper_to_cube_pos', 'object-state', 'robot0_eef_pos', 'robot0_eef_quat', 'robot0_eef_quat_site', 'robot0_gripper_qpos', 'robot0_gripper_qvel', 'robot0_joint_acc', 'robot0_joint_pos', 'robot0_joint_pos_cos', 'robot0_joint_pos_sin', 'robot0_joint_vel', 'robot0_proprio-state']
{'robot0_joint_pos': (7,), 'robot0_joint_pos_cos': (7,), 'robot0_joint_pos_sin': (7,), 'robot0_joint_vel': (7,), 'robot0_joint_acc': (7,), 'robot0_eef_pos': (3,), 'robot0_eef_quat': (4,), 'robot0_eef_quat_site': (4,), 'robot0_gripper_qpos': (2,), 'robot0_gripper_qvel': (2,), 'cube_pos': (3,), 'cube_quat': (4,), 'gripper_to_cube_pos': (3,), 'robot0_proprio-state': (50,), 'object-state': (10,)}


In [6]:
# Build robosuite Lift env and wrap for flat observations matching dataset/env keys
import robosuite as suite
from robosuite.wrappers import GymWrapper
from stable_baselines3.common.vec_env import DummyVecEnv

# Observation keys to match env dict and map from dataset
DATASET_KEYS = [
    "object-state",  # map from dataset "object"
    "robot0_eef_pos",
    "robot0_eef_quat",
    "robot0_eef_quat_site",
    "robot0_gripper_qpos",
    "robot0_gripper_qvel",
    "robot0_joint_pos",
    "robot0_joint_pos_cos",
    "robot0_joint_pos_sin",
    "robot0_joint_vel",
]

def make_env():
    rs_env = suite.make(
        "Lift",
        robots=["Panda"],
        use_camera_obs=False,
        use_object_obs=True,
        controller_configs=None,
        has_offscreen_renderer=False,
        has_renderer=False,
        render_camera=None,
        control_freq=20,
        horizon=200,
        reward_shaping=True,
        gripper_types="PandaGripper",
    )
    return GymWrapper(rs_env, keys=DATASET_KEYS, flatten_obs=True)

venv = DummyVecEnv([make_env for _ in range(N_ENVS)])
venv.observation_space, venv.action_space

[robosuite INFO] Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json (composite_controller_factory.py:121)
[robosuite INFO] Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json (composite_controller_factory.py:121)
[robosuite INFO] Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json (composite_controller_factory.py:121)
[robosuite INFO] Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json (composite_controller_factory.py:121)
[robosuite INFO] Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json (composi

(Box(-inf, inf, (53,), float32), Box(-1.0, 1.0, (7,), float32))

## Convert expert rollouts to imitation Trajectory objects
Filter the expert observation dicts to the keys present in the Gym env, then stack into DictObs.

In [7]:
# Convert raw_expert to Imitation trajectories (flattened to match env Box obs)
import numpy as np
from imitation.data.types import TrajectoryWithRew
from gymnasium import spaces as _spaces


def to_imitation_trajectories_flat(raw_trajs, obs_space, keys_order):
    assert isinstance(obs_space, _spaces.Box), "Expected flat Box observation space"
    trajs = []
    for ep in raw_trajs:
        if "obs" in ep and "obs_list" not in ep:
            ep["obs_list"] = ep.pop("obs")
        flat_obs_list = []
        for ob in ep["obs_list"]:
            # Map dataset 'object' -> env 'object-state'
            ob_mapped = dict(ob)
            if "object" in ob_mapped and "object-state" not in ob_mapped:
                ob_mapped["object-state"] = ob_mapped["object"]
            parts = []
            for k in keys_order:
                if k in ob_mapped:
                    parts.append(np.asarray(ob_mapped[k]).reshape(-1))
            flat = np.concatenate(parts, axis=0).astype(np.float32)
            flat_obs_list.append(flat)
        obs_arr = np.asarray(flat_obs_list, dtype=np.float32)
        acts = np.asarray(ep["acts"], dtype=np.float32)
        rews = np.asarray(ep.get("rews", np.zeros(len(acts), dtype=np.float32)), dtype=np.float32)
        trajs.append(TrajectoryWithRew(obs=obs_arr, acts=acts, infos=None, rews=rews, terminal=True))
    return trajs

expert_trajs = to_imitation_trajectories_flat(raw_expert, venv.observation_space, DATASET_KEYS)
len(expert_trajs), len(expert_trajs[0].acts)

(200, 59)

## Train AIRL (PPO generator on learned reward)
We set up PPO with a MultiInputPolicy (for dict observations), a simple shaped reward net, and train AIRL.

In [12]:
# BC pretraining: train a small Behavioral Cloning policy and save an SB3-compatible warmstart model
# This makes it explicit in the notebook flow so AIRL can be warm-started.
from imitation.algorithms.bc import BC
from imitation.util import logger as imit_logger
from stable_baselines3 import PPO
import os

bc_epochs = 10  # increase if needed (20-50 for stronger pretraining)
bc_batch_size = 64
bc_minibatch = 32
warm_dir = 'warmstart_ppo'
os.makedirs(warm_dir, exist_ok=True)

assert 'expert_trajs' in globals(), 'expert_trajs not found; run conversion cell first'
print(f'Running BC pretraining for {bc_epochs} epochs on {len(expert_trajs)} demos...')
rng = __import__('numpy').random.default_rng(SEED if 'SEED' in globals() else 0)
bc_logger = imit_logger.configure('bc_pretrain_notebook', ('stdout',))
bc = BC(observation_space=venv.observation_space, action_space=venv.action_space, rng=rng, demonstrations=expert_trajs, batch_size=bc_batch_size, minibatch_size=bc_minibatch, device='cpu', custom_logger=bc_logger)
bc.set_demonstrations(expert_trajs)
bc.train(n_epochs=bc_epochs, log_rollouts_venv=venv, log_rollouts_n_episodes=1, progress_bar=False)
# Build small PPO with matching architecture and copy matching params into it, then save as SB3 model for AIRL warmstart
import torch.nn as nn
try:
    policy_net = bc.policy.mlp_extractor.policy_net
    value_net = bc.policy.mlp_extractor.value_net
    linear_policy = [m for m in policy_net if isinstance(m, nn.Linear)]
    linear_value = [m for m in value_net if isinstance(m, nn.Linear)]
    pi_arch = [int(m.out_features) for m in linear_policy]
    vf_arch = [int(m.out_features) for m in linear_value]
except Exception:
    pi_arch, vf_arch = [64,64], [64,64]
policy_kwargs = dict(net_arch=[dict(pi=pi_arch, vf=vf_arch)])
ppo = PPO('MlpPolicy', venv, verbose=0, policy_kwargs=policy_kwargs, device='cpu')
ppo_pd = ppo.policy.state_dict()
bc_pd = bc.policy.state_dict()
matched = {k:v for k,v in bc_pd.items() if k in ppo_pd and ppo_pd[k].shape == v.shape}
ppo_pd.update(matched)
ppo.policy.load_state_dict(ppo_pd)
ppo.save(os.path.join(warm_dir, 'model'))
print('Saved warmstart PPO to', os.path.join(warm_dir, 'model.zip'))

[robosuite INFO] Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json (composite_controller_factory.py:121)
INFO:robosuite_logs:Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json
[robosuite INFO] Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json (composite_controller_factory.py:121)
INFO:robosuite_logs:Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json


Running BC pretraining for 10 epochs on 200 demos...


[robosuite INFO] Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json (composite_controller_factory.py:121)
INFO:robosuite_logs:Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json
[robosuite INFO] Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json (composite_controller_factory.py:121)
INFO:robosuite_logs:Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json
[robosuite INFO] Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json (composite_controller_factory.py:121)
INFO:robosuite_logs:Loading controller c

--------------------------------
| batch_size        | 32       |
| bc/               |          |
|    batch          | 0        |
|    ent_loss       | -0.00993 |
|    entropy        | 9.93     |
|    epoch          | 0        |
|    l2_loss        | 0        |
|    l2_norm        | 129      |
|    loss           | 7.17     |
|    neglogp        | 7.18     |
|    prob_true_act  | 0.000772 |
|    samples_so_far | 64       |
| rollout/          |          |
|    return_max     | 13.2     |
|    return_mean    | 6.07     |
|    return_min     | 0.48     |
|    return_std     | 5.56     |
--------------------------------


/home/chris/miniconda3/envs/env_lift/lib/python3.11/site-packages/imitation/algorithms/bc.py:236: UserWarning: Converting a tensor with requires_grad=True to a scalar may lead to unexpected behavior.
Consider using tensor.detach() first. (Triggered internally at /pytorch/torch/csrc/autograd/generated/python_variable_methods.cpp:836.)
  self._logger.record(f"bc/{k}", float(v) if v is not None else None)
[robosuite INFO] Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json (composite_controller_factory.py:121)
INFO:robosuite_logs:Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json
[robosuite INFO] Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json (composite_controller_factory.py:121)
INFO:robosu

...

[robosuite INFO] Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json (composite_controller_factory.py:121)
INFO:robosuite_logs:Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json
[robosuite INFO] Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json (composite_controller_factory.py:121)
INFO:robosuite_logs:Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json
[robosuite INFO] Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json (composite_controller_factory.py:121)
INFO:robosuite_logs:Loading controller c

--------------------------------
| batch_size        | 32       |
| bc/               |          |
|    batch          | 1000     |
|    ent_loss       | -0.003   |
|    entropy        | 3        |
|    epoch          | 6        |
|    l2_loss        | 0        |
|    l2_norm        | 200      |
|    loss           | 0.474    |
|    neglogp        | 0.477    |
|    prob_true_act  | 1.21     |
|    samples_so_far | 64064    |
| rollout/          |          |
|    return_max     | 11.2     |
|    return_mean    | 7.02     |
|    return_min     | 1.22     |
|    return_std     | 4.18     |
--------------------------------


[robosuite INFO] Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json (composite_controller_factory.py:121)
INFO:robosuite_logs:Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json
[robosuite INFO] Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json (composite_controller_factory.py:121)
INFO:robosuite_logs:Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json
[robosuite INFO] Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json (composite_controller_factory.py:121)
INFO:robosuite_logs:Loading controller c

--------------------------------
| batch_size        | 32       |
| bc/               |          |
|    batch          | 1500     |
|    ent_loss       | 6.54e-05 |
|    entropy        | -0.0654  |
|    epoch          | 9        |
|    l2_loss        | 0        |
|    l2_norm        | 242      |
|    loss           | -2.77    |
|    neglogp        | -2.77    |
|    prob_true_act  | 25.4     |
|    samples_so_far | 96064    |
| rollout/          |          |
|    return_max     | 17.7     |
|    return_mean    | 13.2     |
|    return_min     | 7.43     |
|    return_std     | 3.67     |
--------------------------------
Saved warmstart PPO to warmstart_ppo/model.zip


/home/chris/miniconda3/envs/env_lift/lib/python3.11/site-packages/stable_baselines3/common/policies.py:484: UserWarning: As shared layers in the mlp_extractor are removed since SB3 v1.8.0, you should now pass directly a dictionary and not a list (net_arch=dict(pi=..., vf=...) instead of net_arch=[dict(pi=..., vf=...)])
  warnings.warn(


In [8]:
# Inspect observation keys in the dataset for mapping
import h5py
import numpy as np

with h5py.File(demo_local, "r") as f:
    data_grp = f["data"]
    first_key = sorted(list(data_grp.keys()))[0]
    g = data_grp[first_key]
    obs_group = g["obs"]
    print("Episode:", first_key)
    for k in obs_group.keys():
        arr = np.array(obs_group[k])
        print(k, arr.shape)
    print("actions:", g["actions"].shape)


Episode: demo_0
object (59, 10)
robot0_eef_pos (59, 3)
robot0_eef_quat (59, 4)
robot0_eef_quat_site (59, 4)
robot0_gripper_qpos (59, 2)
robot0_gripper_qvel (59, 2)
robot0_joint_pos (59, 7)
robot0_joint_pos_cos (59, 7)
robot0_joint_pos_sin (59, 7)
robot0_joint_vel (59, 7)
actions: (59, 7)


In [13]:
# Train AIRL with PPO generator on the learned reward (flat obs)
import os
from stable_baselines3 import PPO
from stable_baselines3.common.evaluation import evaluate_policy
from stable_baselines3.ppo import MlpPolicy

TB_LOG_DIR = "tb_logs/airl"  # TensorBoard log directory (scalars: policy_gradient_loss, value_loss, entropy_loss, etc.)

# If a warm-start SB3 model exists, load it instead of creating a fresh PPO
warm_agent_path = os.path.join('warmstart_ppo', 'model.zip')
if os.path.exists(warm_agent_path):
    print(f'Found warmstart agent at {warm_agent_path}; loading as PPO learner')
    learner = PPO.load(warm_agent_path, env=venv, device='cpu')
else:
    print('No warmstart agent found; creating fresh PPO learner')
    # PPO learner on flat observations (forced CPU to avoid GPU OOM / long-run crashes)
    learner = PPO(
        policy=MlpPolicy,
        env=venv,
        verbose=1,
        n_steps=1024 // N_ENVS,
        batch_size=256,
        n_epochs=10,
        gae_lambda=0.95,
        gamma=0.99,
        device="cpu",  # enforce CPU placement
        tensorboard_log=TB_LOG_DIR,
    )

# Reward net used by the AIRL discriminator
reward_net = BasicShapedRewardNet(
    observation_space=venv.observation_space,
    action_space=venv.action_space,
    normalize_input_layer=RunningNorm,
)

# Determine demo batch size based on available transitions
transitions_count = sum(len(t.acts) for t in expert_trajs)
demo_bs = min(512, max(64, transitions_count // 4))

# Correct logger import (previous error was from a wrong alias name)
from imitation.util import logger as imit_logger
from pathlib import Path
# Configure hierarchical logger with tensorboard so PPO (actor/critic) and discriminator scalars are emitted.
custom_logger = imit_logger.configure(Path(TB_LOG_DIR), ('stdout','log','csv','tensorboard'))

airl_trainer = AIRL(
    demonstrations=expert_trajs,
    demo_batch_size=demo_bs,
    gen_replay_buffer_capacity=max(1024, demo_bs * 2),
    n_disc_updates_per_round=8, # tune
    venv=venv,
    gen_algo=learner,
    reward_net=reward_net,
    allow_variable_horizon=True,  # allow variable-length episodes from demos; see docs for caveats
    custom_logger=custom_logger,  # ensures SB3 logger includes tensorboard writer
    init_tensorboard=True,        # enables discriminator (disc/) summaries (e.g., disc_loss, disc_acc)
    log_dir=TB_LOG_DIR,           # unify logging directory
)

# Evaluate before training (environment reward)
venv.seed(SEED)
mean_pre, std_pre = evaluate_policy(learner, venv, n_eval_episodes=2, deterministic=False)
print(f"Before AIRL training: mean env reward = {mean_pre:.2f} ± {std_pre:.2f}")
print(f"TensorBoard logging to: {TB_LOG_DIR} (run: 'tensorboard --logdir {TB_LOG_DIR}')")

# Train AIRL
# Long single-call training with large N_RL_TRAIN_STEPS can exhaust memory and abort the kernel.
# Instead of calling airl_trainer.train(N_RL_TRAIN_STEPS) directly, use the chunked training
# utility added below (train_airl_in_chunks) for large runs (e.g., 400_000+ steps).
# Uncomment the next line ONLY for small tests (e.g., <= 50_000 steps):
# airl_trainer.train(min(N_RL_TRAIN_STEPS, 50_000))

# Evaluate after (only meaningful if some training was performed)
mean_post, std_post = evaluate_policy(airl_trainer.gen_algo, venv, n_eval_episodes=2, deterministic=False)
print(f"After (partial) AIRL training: mean env reward = {mean_post:.2f} ± {std_post:.2f}")


Found warmstart agent at warmstart_ppo/model.zip; loading as PPO learner
Running with `allow_variable_horizon` set to True. Some algorithms are biased towards shorter or longer episodes, which may significantly confound results. Additionally, even unbiased algorithms can exploit the information leak from the termination condition, producing spuriously high performance. See https://imitation.readthedocs.io/en/latest/getting-started/variable-horizon.html for more information.


[robosuite INFO] Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json (composite_controller_factory.py:121)
INFO:robosuite_logs:Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json
INFO:robosuite_logs:Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json
[robosuite INFO] Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json (composite_controller_factory.py:121)
INFO:robosuite_logs:Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json
[robosuite INFO] Loading controller configuration from: /home/chris/AIRL_Im

Before AIRL training: mean env reward = 11.60 ± 3.61
TensorBoard logging to: tb_logs/airl (run: 'tensorboard --logdir tb_logs/airl')


[robosuite INFO] Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json (composite_controller_factory.py:121)
INFO:robosuite_logs:Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json
INFO:robosuite_logs:Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json
[robosuite INFO] Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json (composite_controller_factory.py:121)
INFO:robosuite_logs:Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json
[robosuite INFO] Loading controller configuration from: /home/chris/AIRL_Im

After (partial) AIRL training: mean env reward = 58.64 ± 43.83


In [14]:
# Warm-up logging round: emit initial actor & discriminator scalars if tensorboard still empty
import glob, os
evt_files = glob.glob(f'{TB_LOG_DIR}/**/events.out.tfevents.*', recursive=True)
if not evt_files:
    print('No TensorBoard event files yet; running one AIRL training round to create them...')
    # One generator round equals airl_trainer.gen_train_timesteps transitions; train() will also do disc updates.
    airl_trainer.train(airl_trainer.gen_train_timesteps)
    new_evt = glob.glob(f'{TB_LOG_DIR}/**/events.out.tfevents.*', recursive=True)
    print(f'Event files created: {len(new_evt)}')
    print('Keys to look for in TensorBoard Scalars: train/policy_gradient_loss, train/value_loss, disc_loss, disc_acc, disc_entropy.')
else:
    print('TensorBoard event files already present; skip warm-up round.')
    print('If discriminator metrics are missing, ensure this cell ran AFTER rebuilding airl_trainer with custom_logger.')

TensorBoard event files already present; skip warm-up round.
If discriminator metrics are missing, ensure this cell ran AFTER rebuilding airl_trainer with custom_logger.


In [15]:
# Chunked AIRL training utility with checkpointing and memory logging
import os, gc, time
import torch

# Optional memory monitor
def _get_mem_mb():
    try:
        import psutil  # type: ignore
        p = psutil.Process(os.getpid())
        return int(p.memory_info().rss / (1024 * 1024))
    except Exception:
        # Fallback using resource (POSIX only)
        try:
            import resource
            return int(resource.getrusage(resource.RUSAGE_SELF).ru_maxrss / 1024)
        except Exception:
            return -1


def train_airl_in_chunks(
    trainer,
    total_steps: int,
    chunk_size: int = 50_000,
    eval_env=None,
    eval_episodes: int = 1,
    checkpoint_every: int | None = 2,
    checkpoint_dir: str = "checkpoints",
):
    """
    Train AIRL in smaller chunks to reduce memory pressure and improve stability.
    - Saves PPO generator policy and reward net periodically.
    - Optionally evaluates after each chunk.
    """
    from stable_baselines3.common.evaluation import evaluate_policy as _eval

    os.makedirs(checkpoint_dir, exist_ok=True)
    n_chunks = max(1, (total_steps + chunk_size - 1) // chunk_size)
    start_time = time.time()
    for i in range(n_chunks):
        remaining = total_steps - i * chunk_size
        steps = int(min(chunk_size, max(0, remaining)))
        if steps <= 0:
            break
        mem = _get_mem_mb()
        print(f"[Chunk {i+1}/{n_chunks}] Training {steps} steps... (RSS={mem} MB)")
        trainer.train(steps)

        # Light evaluation (optional)
        if eval_env is not None and eval_episodes > 0:
            try:
                mean_r, std_r = _eval(trainer.gen_algo, eval_env, n_eval_episodes=eval_episodes, deterministic=False)
                print(f"  Eval after chunk {i+1}: mean env reward = {mean_r:.2f} ± {std_r:.2f}")
            except Exception as e:
                print("  Eval failed:", repr(e))

        # Periodic checkpointing
        if checkpoint_every and ((i + 1) % int(checkpoint_every) == 0):
            total_done = (i + 1) * chunk_size if (i + 1) < n_chunks else total_steps
            try:
                trainer.gen_algo.save(os.path.join(checkpoint_dir, f"ppo_gen_{total_done}.zip"))
            except Exception as e:
                print("  Policy checkpoint failed:", repr(e))
            # Try saving the reward net
            try:
                rn = getattr(trainer, "reward_net", None)
                if rn is None:
                    # fall back to global reward_net if in scope
                    rn = globals().get("reward_net", None)
                if rn is not None:
                    torch.save(rn.state_dict(), os.path.join(checkpoint_dir, f"reward_net_{total_done}.pt"))
            except Exception as e:
                print("  Reward net checkpoint failed:", repr(e))

        # Housekeeping
        gc.collect()
        if torch.cuda.is_available():
            try:
                torch.cuda.empty_cache()
            except Exception:
                pass

    dur = time.time() - start_time
    print(f"Done: {total_steps} steps in {dur/60.0:.1f} min. Last RSS={_get_mem_mb()} MB")

# Example usage for long runs (safe on CPU, resumable via checkpoints):
# train_airl_in_chunks(airl_trainer, total_steps=int(N_RL_TRAIN_STEPS), chunk_size=(5_000 if FAST else 50_000),
#                      eval_env=venv, eval_episodes=1, checkpoint_every=2, checkpoint_dir="checkpoints")

In [16]:
# Start chunked AIRL training (executes training)
CHUNK_SIZE = 5_000 if FAST else 50_000
TOTAL_STEPS = int(N_RL_TRAIN_STEPS)
print(f"Starting chunked AIRL training: total_steps={TOTAL_STEPS}, chunk_size={CHUNK_SIZE}")
if 'train_airl_in_chunks' not in globals():
    print("train_airl_in_chunks not found. Please run the utility cell above to define it.")
else:
    train_airl_in_chunks(
        airl_trainer,
        total_steps=TOTAL_STEPS,
        chunk_size=CHUNK_SIZE,
        eval_env=venv,
        eval_episodes=1,
        checkpoint_every=2,
        checkpoint_dir="checkpoints",
    )
    
    # tensorboard --logdir imitation/docs/tutorials/tb_logs/airl

Starting chunked AIRL training: total_steps=1000000, chunk_size=50000
[Chunk 1/20] Training 50000 steps... (RSS=1995 MB)


round:   0%|          | 0/6 [00:00<?, ?it/s][robosuite INFO] Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json (composite_controller_factory.py:121)
INFO:robosuite_logs:Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json
[robosuite INFO] Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json (composite_controller_factory.py:121)
INFO:robosuite_logs:Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json
[robosuite INFO] Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json (composite_controller_factory.py:1

--------------------------------------
| raw/                        |      |
|    gen/time/fps             | 222  |
|    gen/time/iterations      | 1    |
|    gen/time/time_elapsed    | 36   |
|    gen/time/total_timesteps | 8192 |
--------------------------------------
--------------------------------------------------
| raw/                                |          |
|    disc/disc_acc                    | 0.339    |
|    disc/disc_acc_expert             | 0.0488   |
|    disc/disc_acc_gen                | 0.629    |
|    disc/disc_entropy                | 0.329    |
|    disc/disc_loss                   | 1.97     |
|    disc/disc_proportion_expert_pred | 0.21     |
|    disc/disc_proportion_expert_true | 0.5      |
|    disc/global_step                 | 1        |
|    disc/n_expert                    | 512      |
|    disc/n_generated                 | 512      |
--------------------------------------------------
--------------------------------------------------
| raw/       

round:  17%|█▋        | 1/6 [00:38<03:10, 38.19s/it][robosuite INFO] Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json (composite_controller_factory.py:121)
INFO:robosuite_logs:Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json
[robosuite INFO] Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json (composite_controller_factory.py:121)
INFO:robosuite_logs:Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json
[robosuite INFO] Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json (composite_controller_fact

----------------------------------------------------
| raw/                               |             |
|    gen/rollout/ep_rew_wrapped_mean | -9.72       |
|    gen/time/fps                    | 227         |
|    gen/time/iterations             | 1           |
|    gen/time/time_elapsed           | 35          |
|    gen/time/total_timesteps        | 16384       |
|    gen/train/approx_kl             | 0.020184929 |
|    gen/train/clip_fraction         | 0.264       |
|    gen/train/clip_range            | 0.2         |
|    gen/train/entropy_loss          | 0.16        |
|    gen/train/explained_variance    | -0.17       |
|    gen/train/learning_rate         | 0.0003      |
|    gen/train/loss                  | 0.0757      |
|    gen/train/n_updates             | 10          |
|    gen/train/policy_gradient_loss  | -0.00636    |
|    gen/train/std                   | 0.238       |
|    gen/train/value_loss            | 0.208       |
----------------------------------------------

...

----------------------------------------------------
| raw/                               |             |
|    gen/rollout/ep_rew_wrapped_mean | 506         |
|    gen/time/fps                    | 208         |
|    gen/time/iterations             | 1           |
|    gen/time/time_elapsed           | 39          |
|    gen/time/total_timesteps        | 974848      |
|    gen/train/approx_kl             | 0.030080084 |
|    gen/train/clip_fraction         | 0.355       |
|    gen/train/clip_range            | 0.2         |
|    gen/train/entropy_loss          | 5.27        |
|    gen/train/explained_variance    | 0.839       |
|    gen/train/learning_rate         | 0.0003      |
|    gen/train/loss                  | 428         |
|    gen/train/n_updates             | 1180        |
|    gen/train/policy_gradient_loss  | 0.00699     |
|    gen/train/std                   | 0.138       |
|    gen/train/value_loss            | 1.2e+03     |
----------------------------------------------

round:  83%|████████▎ | 5/6 [03:19<00:40, 40.14s/it][robosuite INFO] Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json (composite_controller_factory.py:121)
INFO:robosuite_logs:Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json
[robosuite INFO] Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json (composite_controller_factory.py:121)
INFO:robosuite_logs:Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json
[robosuite INFO] Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json (composite_controller_fact

----------------------------------------------------
| raw/                               |             |
|    gen/rollout/ep_rew_wrapped_mean | 501         |
|    gen/time/fps                    | 210         |
|    gen/time/iterations             | 1           |
|    gen/time/time_elapsed           | 38          |
|    gen/time/total_timesteps        | 983040      |
|    gen/train/approx_kl             | 0.030540258 |
|    gen/train/clip_fraction         | 0.348       |
|    gen/train/clip_range            | 0.2         |
|    gen/train/entropy_loss          | 5.34        |
|    gen/train/explained_variance    | 0.812       |
|    gen/train/learning_rate         | 0.0003      |
|    gen/train/loss                  | 941         |
|    gen/train/n_updates             | 1190        |
|    gen/train/policy_gradient_loss  | 0.00565     |
|    gen/train/std                   | 0.137       |
|    gen/train/value_loss            | 1.03e+03    |
----------------------------------------------

round: 100%|██████████| 6/6 [03:59<00:00, 39.97s/it]
[robosuite INFO] Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json (composite_controller_factory.py:121)
INFO:robosuite_logs:Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json
[robosuite INFO] Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json (composite_controller_factory.py:121)
INFO:robosuite_logs:Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json
[robosuite INFO] Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json (composite_controller_fac

  Eval after chunk 20: mean env reward = 62.09 ± 0.00
Done: 1000000 steps in 79.1 min. Last RSS=2053 MB


## Results
If everything is wired correctly, the post-training reward should increase compared to pre-training (exact numbers depend on seeds and environment stochasticity).

## Interactive simulations (on-screen viewer)
These cells open a live Robosuite viewer and step the policy in real time. If you’re on a headless server (no DISPLAY), you’ll need X forwarding or a virtual display.

In [17]:
# Helpers for live viewer runs
import os, time
import robosuite as suite
from robosuite.wrappers import GymWrapper


def make_interactive_env_flat(control_freq=20, horizon=200, onscreen=True):
    """
    Create a Lift env for interactive runs.
    - If onscreen=True: use on-screen renderer (requires DISPLAY).
    - If onscreen=False: use offscreen renderer (safe for headless environments).
    """
    rs_env = suite.make(
        "Lift", robots=["Panda"],
        use_camera_obs=False, use_object_obs=True,
        has_offscreen_renderer=not onscreen, has_renderer=onscreen,
        # When offscreen, pick a camera; on-screen viewer ignores render_camera
        render_camera=("agentview" if not onscreen else None),
        control_freq=control_freq, horizon=horizon, reward_shaping=True,
        gripper_types="PandaGripper",
)
    return GymWrapper(rs_env, keys=DATASET_KEYS, flatten_obs=True)


def _reset_env(env):
    """Handle both Gym and Gymnasium reset signatures."""
    res = env.reset()
    if isinstance(res, tuple) and len(res) == 2:
        obs, info = res
    else:
        obs = res
    return obs


def _step_env(env, action):
    """Handle both 4- and 5-tuple step signatures."""
    res = env.step(action)
    if isinstance(res, tuple) and len(res) == 5:
        next_obs, reward, terminated, truncated, info = res
        done = bool(terminated or truncated)
        return next_obs, reward, done, info
    else:
        next_obs, reward, done, info = res
        return next_obs, reward, bool(done), info


def run_interactive(policy, steps=300, deterministic=True, fps=20):
    """
    Run policy in a live viewer if DISPLAY is available; otherwise fall back to
    recording an offscreen video to avoid crashing the kernel on headless setups.
    """
    display_env = os.environ.get("DISPLAY")
    onscreen = display_env not in (None, "")

    if not onscreen:
        print("DISPLAY not set; falling back to offscreen recording instead of on-screen viewer.")
        # Use existing offscreen rollout helper to produce a short video
        try:
            from IPython.display import Video, display  # lazy import
            roll = rollout_and_record(policy, max_steps=min(steps, 200), deterministic=deterministic,
                                      video_path="interactive_fallback.mp4", compute_learned_reward=False)
            display(Video("interactive_fallback.mp4", embed=True, width=256))
            print("Displayed offscreen video fallback. To use the live viewer, run in a session with DISPLAY.")
        except Exception as e:
            print("Offscreen fallback failed:", repr(e))
        return

    # On-screen path
    env = make_interactive_env_flat(control_freq=fps, horizon=steps + 1, onscreen=True)
    obs = _reset_env(env)
    try:
        for t in range(steps):
            try:
                action, _ = policy.predict(obs, deterministic=deterministic)
            except Exception:
                # Some policies (e.g., random) may accept only obs
                action = policy(obs)
            obs, r, done, info = _step_env(env, action)
            # Render the on-screen viewer (try multiple access patterns)
            try:
                env.unwrapped.render()
            except Exception:
                try:
                    env.render()
                except Exception:
                    try:
                        env.unwrapped.env.render()
                    except Exception:
                        pass
            if done:
                obs = _reset_env(env)
            # Keep near-real-time
            time.sleep(max(0.0, 1.0 / float(fps)))
    except KeyboardInterrupt:
        print("Interrupted by user.")
    finally:
        env.close()

In [ ]:
# Simulate BEFORE training (on-screen)
from stable_baselines3 import PPO
from stable_baselines3.ppo import MlpPolicy

pre_policy = PPO(policy=MlpPolicy, env=venv, verbose=0, n_steps=512 // N_ENVS, batch_size=256, n_epochs=1, device="cpu")
print("Running pre-training policy interactively... Close the window or press Ctrl+C to stop.")
run_interactive(pre_policy, steps=300, deterministic=True, fps=20)

In [44]:
# Simulate AFTER training (on-screen)
if 'airl_trainer' in globals():
    print("Running AIRL generator policy interactively... Close the window or press Ctrl+C to stop.")
    # Ensure generator is on CPU
    try:
        airl_trainer.gen_algo.set_device("cpu")
    except Exception:
        pass
    run_interactive(airl_trainer.gen_algo, steps=300, deterministic=True, fps=20)
else:
    print("airl_trainer not found. Please run the training (prefer chunked) cells first.")

[robosuite INFO] Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json (composite_controller_factory.py:121)
INFO:robosuite_logs:Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json
INFO:robosuite_logs:Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json
[robosuite INFO] Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json (composite_controller_factory.py:121)
INFO:robosuite_logs:Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json
[robosuite INFO] Loading controller configuration from: /home/chris/AIRL_Im

Running AIRL generator policy interactively... Close the window or press Ctrl+C to stop.


[robosuite INFO] Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json (composite_controller_factory.py:121)
INFO:robosuite_logs:Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json
INFO:robosuite_logs:Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json


## Augment expert episodes with simulator states (if present in HDF5)

In [ ]:
# Helpers to replay an expert episode by action or state playback (reverted simpler working version)
import os, time
import numpy as np

def _ensure_imageio():
    try:
        import imageio.v2 as imageio  # noqa: F401
        return True
    except Exception:
        try:
            import sys, subprocess
            subprocess.check_call([sys.executable, "-m", "pip", "install", "imageio"])
            import imageio.v2 as imageio  # noqa: F401
            return True
        except Exception as e:
            print("Failed to ensure imageio:", repr(e))
            return False

def make_vis_env_flat(camera="agentview", width=256, height=256):
    import robosuite as suite
    from robosuite.wrappers import GymWrapper
    rs_env = suite.make(
        "Lift", robots=["Panda"],
        use_camera_obs=False, use_object_obs=True,
        has_offscreen_renderer=True, has_renderer=False,
        render_camera=camera,
        control_freq=20, horizon=200, reward_shaping=True,
        gripper_types="PandaGripper",
)
    return GymWrapper(rs_env, keys=DATASET_KEYS, flatten_obs=True)

def _get_rs_env(env):
    base = getattr(env, "unwrapped", env)
    return getattr(base, "env", base)

def _get_sim(env):
    rs_env = _get_rs_env(env)
    sim = getattr(rs_env, "sim", None)
    if sim is None:
        sim = getattr(rs_env, "mj_sim", None)
    return sim

def _safe_render(env):
    for fn in [lambda e: _get_rs_env(e).render(), lambda e: e.unwrapped.render(), lambda e: e.render()]:
        try:
            fn(env)
            return True
        except Exception:
            pass
    return False

def _set_sim_state_from_flat(sim, flat):
    try:
        nq = int(sim.model.nq)
        nv = int(sim.model.nv)
        flat = np.asarray(flat, dtype=np.float64).ravel()
        qpos = flat[:nq]
        qvel = flat[nq:nq+nv]
        try:
            import mujoco as mj  # type: ignore
            sim.data.qpos[:nq] = qpos
            sim.data.qvel[:nv] = qvel
            mj.mj_forward(sim.model, sim.data)
            return True
        except Exception:
            pass
        try:
            state = sim.get_state()
            state.qpos[:] = qpos
            state.qvel[:] = qvel
            sim.set_state(state)
            sim.forward()
            return True
        except Exception:
            return False
    except Exception:
        return False

def _find_cube_free_joint(sim):
    try:
        import mujoco as mj  # type: ignore
        nj = sim.model.njnt
        for j in range(nj):
            if int(sim.model.jnt_type[j]) != 0:
                continue
            body_id = int(sim.model.jnt_bodyid[j])
            try:
                jname = mj.mj_id2name(sim.model, mj.mjtObj.mjOBJ_JOINT, j) or ""
            except Exception:
                jname = ""
            try:
                bname = mj.mj_id2name(sim.model, mj.mjtObj.mjOBJ_BODY, body_id) or ""
            except Exception:
                bname = ""
            name_str = (jname + ":" + bname).lower()
            if any(tok in name_str for tok in ["cube", "object0", "object"]):
                adr = int(sim.model.jnt_qposadr[j])
                return (jname or bname or "freejoint"), adr
    except Exception:
        pass
    try:
        nj = sim.model.njnt
        for j in range(nj):
            if int(sim.model.jnt_type[j]) != 0:
                continue
            try:
                b_id = int(sim.model.jnt_bodyid[j])
            except Exception:
                b_id = None
            try:
                jname = sim.model.id2name(j, 'joint')
            except Exception:
                jname = None
            try:
                bname = sim.model.id2name(b_id, 'body') if b_id is not None else None
            except Exception:
                bname = None
            name_str = ((jname or "") + ":" + (bname or "")).lower()
            if any(tok in name_str for tok in ["cube", "object0", "object"]):
                adr = int(sim.model.jnt_qposadr[j])
                return (jname or bname or "freejoint"), adr
    except Exception:
        pass
    return (None, None)

def _try_align_initial_cube_pose_from_obs(sim, ep):
    try:
        obs_list = None
        if isinstance(ep, dict):
            if 'obs_list' in ep and isinstance(ep['obs_list'], (list, tuple)) and len(ep['obs_list']) > 0:
                obs_list = ep['obs_list']
            elif 'obs' in ep and isinstance(ep['obs'], (list, tuple)) and len(ep['obs']) > 0:
                obs_list = ep['obs']
        if obs_list is None:
            return False
        ob0 = obs_list[0]
        if not isinstance(ob0, dict):
            return False
        pos = None
        quat = None
        if 'cube_pos' in ob0:
            pos = np.asarray(ob0['cube_pos']).astype(np.float64)
        if 'cube_quat' in ob0:
            quat = np.asarray(ob0['cube_quat']).astype(np.float64)
        if pos is None:
            for key in ['object', 'object-state']:
                if key in ob0 and len(np.asarray(ob0[key]).ravel()) >= 3:
                    v = np.asarray(ob0[key]).ravel()
                    pos = v[:3].astype(np.float64)
                    if len(v) >= 7:
                        quat = v[3:7].astype(np.float64)
                    break
        if pos is None:
            return False
        qpos7 = np.zeros(7, dtype=np.float64)
        qpos7[:3] = pos
        if quat is not None and len(quat) == 4:
            qpos7[3:] = np.array([quat[3], quat[0], quat[1], quat[2]], dtype=np.float64)
        else:
            qpos7[3:] = np.array([1.0, 0.0, 0.0, 0.0], dtype=np.float64)
        jname, adr = _find_cube_free_joint(sim)
        if adr is None:
            return False
        sim.data.qpos[adr:adr+7] = qpos7
        try:
            import mujoco as mj  # type: ignore
            mj.mj_forward(sim.model, sim.data)
        except Exception:
            sim.forward()
        return True
    except Exception:
        return False

def replay_expert_trajectory(ep, onscreen=None, fps=20, max_steps=None, camera="agentview", width=256, height=256, video_path="expert_replay.mp4"):
    if onscreen is None:
        onscreen = os.environ.get("DISPLAY") not in (None, "")
    acts = np.asarray(ep.get("acts", []), dtype=np.float32)
    states = ep.get("states", None)

    # State-driven
    if states is not None and len(states) > 0:
        states = np.asarray(states)
        steps = len(states) if max_steps is None else min(len(states), int(max_steps))
        if not onscreen:
            if not _ensure_imageio():
                print("imageio missing; aborting video record.")
                return {}
            import imageio.v2 as imageio
            env = make_vis_env_flat(camera=camera, width=width, height=height)
            _ = _reset_env(env)
            sim = _get_sim(env)
            frames = []
            for t in range(steps):
                _set_sim_state_from_flat(sim, states[t])
                try:
                    frame = sim.render(width=width, height=height, camera_name=camera)
                except Exception:
                    frame = np.zeros((height, width, 3), dtype=np.uint8)
                frames.append(frame)
            imageio.mimwrite(video_path, frames, fps=fps)
            try:
                from IPython.display import Video, display
                display(Video(video_path, embed=True, width=width))
            except Exception:
                pass
            env.close()
            return {"video_path": video_path}
        else:
            env = make_interactive_env_flat(control_freq=fps, horizon=steps + 1, onscreen=True)
            _ = _reset_env(env)
            sim = _get_sim(env)
            try:
                for t in range(steps):
                    _set_sim_state_from_flat(sim, states[t])
                    _safe_render(env)
                    time.sleep(max(0.0, 1.0 / float(fps)))
            except KeyboardInterrupt:
                print("Interrupted.")
            finally:
                env.close()
            return {}

    # Action-driven fallback
    steps = len(acts) if max_steps is None else min(len(acts), int(max_steps))
    if not onscreen:
        if not _ensure_imageio():
            print("imageio missing; aborting video record.")
            return {}
        import imageio.v2 as imageio
        env = make_vis_env_flat(camera=camera, width=width, height=height)
        obs = _reset_env(env)
        _try_align_initial_cube_pose_from_obs(_get_sim(env), ep)
        sim = _get_sim(env)
        frames = []
        try:
            frame0 = sim.render(width=width, height=height, camera_name=camera)
        except Exception:
            frame0 = np.zeros((height, width, 3), dtype=np.uint8)
        frames.append(frame0)
        for t in range(steps):
            obs, r, done, info = _step_env(env, acts[t])
            try:
                frm = sim.render(width=width, height=height, camera_name=camera)
            except Exception:
                frm = np.zeros((height, width, 3), dtype=np.uint8)
            frames.append(frm)
            if done:
                break
        imageio.mimwrite(video_path, frames, fps=fps)
        try:
            from IPython.display import Video, display
            display(Video(video_path, embed=True, width=width))
        except Exception:
            pass
        env.close()
        return {"video_path": video_path}
    else:
        env = make_interactive_env_flat(control_freq=fps, horizon=steps + 1, onscreen=True)
        obs = _reset_env(env)
        _try_align_initial_cube_pose_from_obs(_get_sim(env), ep)
        try:
            for t in range(steps):
                obs, r, done, info = _step_env(env, acts[t])
                _safe_render(env)
                if done:
                    break
                time.sleep(max(0.0, 1.0 / float(fps)))
        except KeyboardInterrupt:
            print("Interrupted.")
        finally:
            env.close()
        return {}

## Expert trajectory replay (on-screen or offscreen fallback)

Replay the expert demonstrations by stepping the environment with the recorded action sequences.
- If a display is available, an on-screen Robosuite viewer will open.
- If running headless, we automatically record an offscreen video and show it inline.

In [ ]:
# Run expert trajectory replay (state-driven when available)
try:
    episodes
except NameError:
    episodes = None
if (episodes is None) and ('raw_expert' in globals()):
    episodes = raw_expert
if (episodes is None) and ('RAW_EXPERT_FROM_DATASET' in globals()):
    episodes = RAW_EXPERT_FROM_DATASET

if episodes is None or len(episodes) == 0:
    print("No expert episodes available to replay. Ensure demos are loaded above.")
else:
    ep_idx = 0  # change this index to replay a different episode
    ep = episodes[ep_idx]
    has_states = isinstance(ep, dict) and ("states" in ep) and (len(ep["states"]) > 0)
    mode = "state-driven" if has_states else "action-driven"
    n_steps = (len(ep["states"]) if has_states else len(ep.get("acts", [])))
    print(f"Replaying expert episode {ep_idx} ({mode}) with {n_steps} steps...")
    replay_expert_trajectory(ep, onscreen=None, fps=20, max_steps=None, camera="agentview", width=256, height=256, video_path="expert_replay.mp4")

In [45]:
# Device verification (quick sanity check)
import torch

def _param_device(module):
    try:
        return next(module.parameters()).device
    except Exception:
        return None

print("learner device:", getattr(learner, "device", None))
print("reward_net device:", _param_device(reward_net))
print("pre_policy device:", getattr(globals().get("pre_policy", None), "device", None))
print("generator (airl_trainer.gen_algo) device:", getattr(globals().get("airl_trainer", None).gen_algo, "device", None) if 'airl_trainer' in globals() else None)

learner device: cpu
reward_net device: cpu
pre_policy device: None
generator (airl_trainer.gen_algo) device: cpu


In [ ]:
# Train SAC with the learned AIRL reward
# This cell wraps the robosuite Lift env so that env.step returns the learned AIRL reward from your reward_net.
# It can recover the latest saved reward_net checkpoint automatically if the object is not in memory (fresh kernel).
import os, glob, gymnasium as gym
import numpy as np
import torch
from stable_baselines3 import SAC
from stable_baselines3.common.vec_env import DummyVecEnv
from stable_baselines3.common.evaluation import evaluate_policy

# --- Ensure env factory exists (for fresh sessions) ---
if 'make_env' not in globals():
    # Recreate the minimal env factory matching earlier cells
    import robosuite as suite
    from robosuite.wrappers import GymWrapper
    # Observation keys consistent with earlier config
    DATASET_KEYS = [
        "object-state",
        "robot0_eef_pos",
        "robot0_eef_quat",
        "robot0_eef_quat_site",
        "robot0_gripper_qpos",
        "robot0_gripper_qvel",
        "robot0_joint_pos",
        "robot0_joint_pos_cos",
        "robot0_joint_pos_sin",
        "robot0_joint_vel",
    ]
    def make_env():
        rs_env = suite.make(
            "Lift",
            robots=["Panda"],
            use_camera_obs=False,
            use_object_obs=True,
            controller_configs=None,
            has_offscreen_renderer=False,
            has_renderer=False,
            render_camera=None,
            control_freq=20,
            horizon=200,
            reward_shaping=True,
            gripper_types="PandaGripper",
        )
        return GymWrapper(rs_env, keys=DATASET_KEYS, flatten_obs=True)

# --- Ensure reward_net exists; if not, load newest checkpoint ---
from imitation.rewards.reward_nets import BasicShapedRewardNet
from imitation.util.networks import RunningNorm

if 'reward_net' not in globals() or reward_net is None:
    print("reward_net not found in memory; trying to load latest checkpoint from 'checkpoints/'.")
    # Create a temp env to obtain spaces for constructing the network
    _tmp_env = make_env()
    obs_space = _tmp_env.observation_space
    act_space = _tmp_env.action_space
    reward_net = BasicShapedRewardNet(
        observation_space=obs_space,
        action_space=act_space,
        normalize_input_layer=RunningNorm,
    )
    ckpt_dir = "checkpoints"
    os.makedirs(ckpt_dir, exist_ok=True)
    # Candidate files
    cands = []
    cands += glob.glob(os.path.join(ckpt_dir, "reward_net_*.pt"))
    cands += [p for p in [os.path.join(ckpt_dir, "reward_net_final.pt"), os.path.join(ckpt_dir, "reward_net_latest.pt")] if os.path.exists(p)]
    # Resolve 'latest' symlink if present
    latest_link = os.path.join(ckpt_dir, "latest")
    if os.path.islink(latest_link):
        try:
            p = os.readlink(latest_link)
            # common patterns: latest -> reward_net_xxx.pt
            if os.path.isfile(os.path.join(ckpt_dir, p)):
                cands.append(os.path.join(ckpt_dir, p))
        except Exception:
            pass
    if not cands:
        raise AssertionError("No reward net checkpoint found under 'checkpoints/'. Train AIRL first or place a reward_net_*.pt there.")
    latest = max(cands, key=os.path.getmtime)
    state = torch.load(latest, map_location='cpu')
    reward_net.load_state_dict(state)
    reward_net.eval()
    print(f"Loaded reward_net from: {latest}")
else:
    reward_net.eval()

# Helper to compute learned reward using full transition (s,a,s',done)
@torch.no_grad()
def _compute_learned_reward(s, a, s2, d):
    s_t = torch.as_tensor(s, dtype=torch.float32).unsqueeze(0)
    a_t = torch.as_tensor(a, dtype=torch.float32).unsqueeze(0)
    s2_t = torch.as_tensor(s2, dtype=torch.float32).unsqueeze(0)
    # Try bool then float done types for compatibility across imitation versions
    try:
        d_t = torch.as_tensor([bool(d)], dtype=torch.bool)
        out = reward_net(s_t, a_t, s2_t, d_t)
    except TypeError:
        d_t = torch.as_tensor([float(d)], dtype=torch.float32)
        out = reward_net(s_t, a_t, s2_t, d_t)
    # out may be shape [1] or scalar tensor
    try:
        return float(out.squeeze().cpu().numpy())
    except Exception:
        return float(out.squeeze().cpu().item())

class LearnedRewardWrapper(gym.Env):
    """Gymnasium-style wrapper that replaces the environment's reward with reward_net(s, a, s2, done).
    Attaches original reward in info['orig_reward'] and learned reward in info['learned_reward'].
    """
    metadata = {"render_modes": []}
    def __init__(self, base_env):
        self.base_env = base_env
        self.observation_space = base_env.observation_space
        self.action_space = base_env.action_space
        self._last_obs = None
    def reset(self, *, seed=None, options=None):
        if seed is not None:
            try:
                self.base_env.reset(seed=seed)
            except TypeError:
                pass
        res = self.base_env.reset()
        obs = res[0] if isinstance(res, tuple) else res
        self._last_obs = obs
        info = {} if isinstance(res, tuple) else {}
        return obs, info
    def step(self, action):
        res = self.base_env.step(action)
        if len(res) == 5:  # Gymnasium signature
            next_obs, env_r, terminated, truncated, info = res
            done = bool(terminated or truncated)
        else:  # Gym legacy
            next_obs, env_r, done, info = res
            terminated, truncated = done, False
        learned_r = _compute_learned_reward(self._last_obs, action, next_obs, done)
        info = dict(info)
        info['orig_reward'] = float(env_r)
        info['learned_reward'] = float(learned_r)
        self._last_obs = next_obs
        return next_obs, float(learned_r), terminated, truncated, info
    def render(self):
        try:
            return self.base_env.render()
        except Exception:
            return None
    def close(self):
        try:
            self.base_env.close()
        except Exception:
            pass

# Build vector env with a fresh wrapper instance
vec_env = DummyVecEnv([lambda: LearnedRewardWrapper(make_env())])

SAC_LOG_DIR = "tb_logs/sac_learned_reward"
SAC_STEPS = 200_000  # adjust as desired

sac_model = SAC(
    policy="MlpPolicy",
    env=vec_env,
    learning_rate=3e-4,
    buffer_size=500_000,
    batch_size=256,
    tau=0.02,
    gamma=0.99,
    train_freq=(1, "step"),
    gradient_steps=1,
    target_update_interval=1,
    ent_coef="auto",
    verbose=1,
    tensorboard_log=SAC_LOG_DIR,
    device="cpu",
)

print(f"Training SAC for {SAC_STEPS} steps on learned reward...")
sac_model.learn(total_timesteps=SAC_STEPS, progress_bar=True)

# Light evaluation using learned reward + original env reward capture
def evaluate_dual(model, episodes=3):
    env = make_env()  # raw env for original reward eval
    raw_returns = []
    learned_returns = []
    for ep in range(episodes):
        res = env.reset()
        prev_obs = res[0] if isinstance(res, tuple) else res
        done = False
        ep_raw = 0.0
        ep_learned = 0.0
        while not done:
            action, _ = model.predict(prev_obs, deterministic=True)
            res = env.step(action)
            if len(res) == 5:
                next_obs, r_raw, terminated, truncated, info = res
                done = bool(terminated or truncated)
            else:
                next_obs, r_raw, done, info = res
            lr = _compute_learned_reward(prev_obs, action, next_obs, done)
            ep_raw += float(r_raw)
            ep_learned += float(lr)
            prev_obs = next_obs
        raw_returns.append(ep_raw)
        learned_returns.append(ep_learned)
    env.close()
    return raw_returns, learned_returns

raw_ret, learned_ret = evaluate_dual(sac_model, episodes=3)
print("Eval (original env reward):", raw_ret)
print("Eval (learned reward sum):", learned_ret)
print(f"Means: raw={np.mean(raw_ret):.2f} learned={np.mean(learned_ret):.2f}")

# Save SAC model
os.makedirs("checkpoints", exist_ok=True)
sac_model.save("checkpoints/sac_learned_reward_final.zip")
print("Saved SAC model: checkpoints/sac_learned_reward_final.zip")


[robosuite INFO] Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json (composite_controller_factory.py:121)
INFO:robosuite_logs:Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json
INFO:robosuite_logs:Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json
[robosuite INFO] Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json (composite_controller_factory.py:121)
INFO:robosuite_logs:Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json
[robosuite INFO] Loading controller configuration from: /home/chris/AIRL_Im

Using cpu device
Training SAC for 200000 steps on learned reward...
Logging to tb_logs/sac_learned_reward/SAC_1


Output()

[robosuite INFO] Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json (composite_controller_factory.py:121)
INFO:robosuite_logs:Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json
INFO:robosuite_logs:Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json


[robosuite INFO] Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json (composite_controller_factory.py:121)
INFO:robosuite_logs:Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json
INFO:robosuite_logs:Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json


...

[robosuite INFO] Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json (composite_controller_factory.py:121)
INFO:robosuite_logs:Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json
INFO:robosuite_logs:Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json


[robosuite INFO] Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json (composite_controller_factory.py:121)
INFO:robosuite_logs:Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json
INFO:robosuite_logs:Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json


[robosuite INFO] Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json (composite_controller_factory.py:121)
INFO:robosuite_logs:Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json
INFO:robosuite_logs:Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json


[robosuite INFO] Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json (composite_controller_factory.py:121)
INFO:robosuite_logs:Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json
INFO:robosuite_logs:Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json


---------------------------------
| time/              |          |
|    episodes        | 836      |
|    fps             | 83       |
|    time_elapsed    | 1998     |
|    total_timesteps | 167200   |
| train/             |          |
|    actor_loss      | -958     |
|    critic_loss     | 1.42e+03 |
|    ent_coef        | 0.413    |
|    ent_coef_loss   | 0.0628   |
|    learning_rate   | 0.0003   |
|    n_updates       | 167099   |
---------------------------------


In [ ]:
# Visualize a trained SAC agent on Robosuite Lift.
# - Auto-loads latest SAC checkpoint if not in memory.
# - Uses existing `run_interactive(policy, ...)` helper if available.
# - Otherwise runs a robust fallback:
#   * On-screen viewer if DISPLAY is set
#   * Offscreen video recording if headless

import os
import glob
import time
import numpy as np
from stable_baselines3 import SAC

# -------- Load or reuse SAC model --------
def _load_sac_checkpoint():
    # Preferred default
    candidates = []
    if os.path.exists("checkpoints/sac_learned_reward_final.zip"):
        candidates.append("checkpoints/sac_learned_reward_final.zip")
    # Other likely names
    candidates += sorted(glob.glob("checkpoints/sac_*reward*.zip"))
    candidates += sorted(glob.glob("checkpoints/sac*.zip"))

    if not candidates:
        raise FileNotFoundError(
            "No SAC checkpoint found in 'checkpoints/'. Train SAC first or place a .zip there."
        )
    # Pick the most recent by mtime
    latest = max(candidates, key=os.path.getmtime)
    print(f"Loading SAC model from {latest} ...")
    return SAC.load(latest, device="cpu")

if "sac_model" not in globals() or sac_model is None:
    sac_model = _load_sac_checkpoint()

# -------- Use existing helper if available --------
if "run_interactive" in globals():
    print("Running SAC policy with existing run_interactive(...) helper ...")
    run_interactive(sac_model, steps=300, deterministic=True, fps=20)

else:
    # -------- Minimal self-contained fallback (viewer or offscreen) --------
    print("run_interactive helper not found; using local fallback viewer.")

    import robosuite as suite
    from robosuite.wrappers import GymWrapper

    # Keys consistent with earlier cells; define if missing
    if "DATASET_KEYS" not in globals():
        DATASET_KEYS = [
            "object-state",
            "robot0_eef_pos",
            "robot0_eef_quat",
            "robot0_eef_quat_site",
            "robot0_gripper_qpos",
            "robot0_gripper_qvel",
            "robot0_joint_pos",
            "robot0_joint_pos_cos",
            "robot0_joint_pos_sin",
            "robot0_joint_vel",
        ]

    def _make_env(onscreen: bool, steps: int = 300, fps: int = 20):
        rs_env = suite.make(
            "Lift",
            robots=["Panda"],
            use_camera_obs=False,
            use_object_obs=True,
            has_offscreen_renderer=(not onscreen),
            has_renderer=onscreen,
            render_camera=("agentview" if not onscreen else None),
            control_freq=fps,
            horizon=steps + 1,
            reward_shaping=True,
            gripper_types="PandaGripper",
        )
        return GymWrapper(rs_env, keys=DATASET_KEYS, flatten_obs=True), rs_env

    def _reset_env(env):
        res = env.reset()
        return res[0] if (isinstance(res, tuple) and len(res) == 2) else res

    def _step_env(env, action):
        res = env.step(action)
        if isinstance(res, tuple) and len(res) == 5:
            next_obs, reward, terminated, truncated, info = res
            done = bool(terminated or truncated)
            return next_obs, float(reward), done, info
        else:
            next_obs, reward, done, info = res
            return next_obs, float(reward), bool(done), info

    # Choose path based on DISPLAY
    headless = os.environ.get("DISPLAY") in (None, "")
    steps = 300
    fps = 20

    if headless:
        print("DISPLAY not set; recording an offscreen video (short) instead of on-screen viewer.")
        try:
            from IPython.display import Video, display
            try:
                import imageio.v2 as imageio
            except Exception:
                import sys, subprocess
                subprocess.check_call([sys.executable, "-m", "pip", "install", "imageio"])
                import imageio.v2 as imageio

            env, rs_env = _make_env(onscreen=False, steps=steps, fps=fps)
            obs = _reset_env(env)
            sim = getattr(rs_env, "sim", None)

            frames = []
            for t in range(min(steps, 200)):
                action, _ = sac_model.predict(obs, deterministic=True)
                obs, _, done, _ = _step_env(env, action)
                if sim is not None:
                    try:
                        frame = sim.render(width=256, height=256, camera_name="agentview")
                    except Exception:
                        frame = np.zeros((256, 256, 3), dtype=np.uint8)
                else:
                    frame = np.zeros((256, 256, 3), dtype=np.uint8)
                frames.append(frame)
                if done:
                    obs = _reset_env(env)

            video_path = "sac_interactive_fallback.mp4"
            imageio.mimwrite(video_path, frames, fps=fps)
            try:
                display(Video(video_path, embed=True, width=256))
            except Exception:
                pass
            env.close()
            print(f"Offscreen SAC rollout video saved to {video_path}")

        except Exception as e:
            print("Offscreen visualization failed:", repr(e))

    else:
        print("DISPLAY detected; starting on-screen interactive SAC run...")
        env, _ = _make_env(onscreen=True, steps=steps, fps=fps)
        obs = _reset_env(env)
        try:
            for t in range(steps):
                action, _ = sac_model.predict(obs, deterministic=True)
                obs, _, done, _ = _step_env(env, action)
                # Try multiple render access paths for robustness
                try:
                    env.unwrapped.render()
                except Exception:
                    try:
                        env.render()
                    except Exception:
                        try:
                            env.unwrapped.env.render()
                        except Exception:
                            pass
                if done:
                    obs = _reset_env(env)
                time.sleep(max(0.0, 1.0 / float(fps)))
        except KeyboardInterrupt:
            print("Interrupted by user.")
        finally:
            env.close()

[robosuite INFO] Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json (composite_controller_factory.py:121)
[robosuite INFO] Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json (composite_controller_factory.py:121)
[robosuite INFO] Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json (composite_controller_factory.py:121)


run_interactive helper not found; using local fallback viewer.
DISPLAY detected; starting on-screen interactive SAC run...


[robosuite INFO] Loading controller configuration from: /home/chris/AIRL_Imitation_Robosuite_Robomimic/robosuite/robosuite/controllers/config/robots/default_panda.json (composite_controller_factory.py:121)
